In [1]:
import pyspark as ps
import pandas as pd
import requests
import numpy as np
from bs4 import BeautifulSoup
from scipy import stats
import urllib.request as urllib_request
from urllib.request import Request, urlopen, urlretrieve
from urllib.request import Request, urlopen
from urllib.error import URLError, HTTPError
import time

In [2]:
## config

pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 300)

In [3]:
# iniciando variaveis;

df = pd.DataFrame()

headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36',
    'Accept': 'application/json',
    'Accept-Language': 'pt-BR,en;q=0.5',
    'Connection': 'keep-alive',
    'Referer': 'https://www.webmotors.com.br/',
    'Origin': 'https://www.webmotors.com.br'
}

### Objetivo: ler os dados de uma pesquisa na webmotors para análise de dados;

In [4]:
# API headers/call test;

sesh = requests.Session()
r2 = sesh.get('https://www.webmotors.com.br', headers = headers)
r2.status_code

200

<h2> API Call Function </h2>

In [5]:
raw_result = {}

def api_call(page_num):

    assert page_num > 0

    url = f"""https://www.webmotors.com.br/api/search/car?url=https://www.webmotors.com.br/carros-usados%2Festoque%3Flkid%3D1022%26tipoveiculo%3Dcarros-usados&actualPage={page_num}&displayPerPage=1000&order=1&showMenu=true&showCount=true&showBreadCrumb=true&testAB=false&returnUrl=false&pandora=false&estadocidade=S%C3%A3o%20Paulo&opcionais=Bancos%20em%20couro&precoate=90000"""


    session = requests.Session()
    r = session.get(url, headers=headers)
    

    df_page = pd.json_normalize(r.json()['SearchResults'])
    raw_result[page_num] = r.json()

    return df_page


# Scraping all search pages;


In [6]:

for page_num in range(1, 5):
    

    df_page_n = api_call(page_num)
    assert df_page_n.empty == False

    df = pd.concat([df, df_page_n])


In [7]:
df.head(2)

UniqueId                                          PhotoPath ListingType  \
0  55143789  2024/202411/20241114/jeep-compass-2-0-16v-flex...           U   
1  55393242  2024/202411/20241105/volkswagen-tiguan-2-0-tsi...           U   

  ProductCode                           Channels  \
0        2611  [{'id': 0, 'Value': 'Webmotors'}]   
1        2611  [{'id': 0, 'Value': 'Webmotors'}]   

                                         LongComment  FipePercent GoodDeal  \
0  - COMPLETO COM PACK PREMIUM\n- REVISADO\n- Loj...         97.0     True   
1  Carro Blindado Nível 3A - Trabalhamos com toda...        104.0      NaN   

   IsElegibleVehicleInspection  IsElegible360View  \
0                         True               True   
1                        False               True   

                                        Media.Photos  \
0  [{'PhotoPath': '2024/202411/20241114/jeep-comp...   
1  [{'PhotoPath': '2024/202411/20241105/volkswage...   

                                 Specification.Title  Specification.Make.id  \
0     JEEP COMPASS 2.0 16V FLEX LONGITUDE AUTOMÁTICO                    218   
1  VOLKSWAGEN TIGUAN 2.0 TSI 16V TURBO GASOLINA 4...                      5   

  Specification.Make.Value  Specification.Model.id Specification.Model.Value  \
0                     JEEP                    3296                   COMPASS   
1               VOLKSWAGEN                    2966                    TIGUAN   

   Specification.Version.id              Specification.Version.Value  \
0                    346882        2.0 16V FLEX LONGITUDE AUTOMÁTICO   
1                    343235  2.0 TSI 16V TURBO GASOLINA 4P TIPTRONIC   

  Specification.YearFabrication  Specification.YearModel  \
0                          2018                   2018.0   
1                          2014                   2015.0   

   Specification.Odometer Specification.Transmission  \
0                 90000.0                 Automática   
1                 99800.0                 Automática   

  Specification.NumberPorts Specification.BodyType  \
0                         4   Utilitário esportivo   
1                         4   Utilitário esportivo   

                     Specification.VehicleAttributes Specification.Armored  \
0  [{'Name': 'Aceita troca'}, {'Name': 'Todas as ...                     N   
1                         [{'Name': 'Aceita troca'}]                     S   

  Specification.Color.IdPrimary Specification.Color.Primary  Seller.Id  \
0                         30404                      Branco    3882943   
1                         30410                       Preto    3882328   

  Seller.SellerType     Seller.City         Seller.State  Seller.AdType.id  \
0                PJ  Rio de Janeiro  Rio de Janeiro (RJ)                 1   
1                PJ       São Paulo       São Paulo (SP)                 1   

  Seller.AdType.Value  Seller.BudgetInvestimento  Seller.DealerScore  \
0                Loja                         -1                   0   
1                Loja                          0                   0   

   Seller.CarDelivery  Seller.TrocaComTroco  Seller.ExceededPlan  \
0                True                  True                False   
1               False                 False                False   

  Seller.FantasyName                                Seller.Localization  \
0               BCAR  [{'State': 'Rio de Janeiro (RJ)', 'City': 'Rio...   
1   MARQUES VEICULOS  [{'State': 'São Paulo (SP)', 'City': 'São Paul...   

   Prices.Price  Prices.SearchPrice                                    HotDeal  
0       89900.0             89900.0                                        NaN  
1       74700.0             74700.0  [{'Id': '1772', 'Value': 'Black Feirão'}]

In [8]:
# vamos armazenar o raw_result em banco de dados NOSQL. Utilizaremos o mesmo para lidar com o problema do limite de requests. Dessa forma, precisaremos saber se os resultados vem em ordem aleatoria ou nao. 
# talvez uma saida seja ordenar os resultados diretamente na API por preço ou km rodada, por exemplo. E usar o Id para checking para nao duplicar dados;
# ordenar por KM faz mais sentido pois um mesmo carro pode variar seu preço, mas a km nao deve mudar (ao menos, em bem menor frequencia;)

type(raw_result)


dict

In [9]:
from app.mongodb_con import PyMongo


In [10]:

db = PyMongo()

db.insert_one('foo', 'cars_price', raw_result)


ServerSelectionTimeoutError: localhost:27017: [Errno 111] Connection refused (configured timeouts: socketTimeoutMS: 20000.0ms, connectTimeoutMS: 20000.0ms), Timeout: 30s, Topology Description: <TopologyDescription id: 6740ef916e8ff1a0e4496124, topology_type: Unknown, servers: [<ServerDescription ('localhost', 27017) server_type: Unknown, rtt: None, error=AutoReconnect('localhost:27017: [Errno 111] Connection refused (configured timeouts: socketTimeoutMS: 20000.0ms, connectTimeoutMS: 20000.0ms)')>]>

In [ ]:
for page, result in raw_result.items():
    
    db.insert_many(
            result['SearchResults']
        )

    break

{'SearchResults': [{'UniqueId': 55586476,
   'Media': {'Photos': [{'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem18001425187.jpg',
      'Order': 1},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem18001531591.jpg',
      'Order': 2},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem1800167898.jpg',
      'Order': 3},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem18001807670.jpg',
      'Order': 4},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem18001942355.jpg',
      'Order': 5},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem1800208100.jpg',
      'Order': 6},
     {'PhotoPath': '2024\\202411\\20241108\\nissan-kicks-1.6-16v-flexstart-sv-4p-xtronic-wmimagem18002229090.jpg',
      'Order': 7},
   

InvalidDocument: documents must have only string keys, key was 1

In [ ]:
asdasd

<h2> EDA </h2> 

In [ ]:
print(f"Número de linhas no df: {df.shape[0]}")

In [ ]:
df.iloc[0]

<h3> COLUMNS OF INTEREST </h3>

In [ ]:
import re
[re.search('Specification.+', x).group(0) for x in df.columns if re.search('Specification', x)]

In [ ]:
cols = [
        'UniqueId', 
        'ProductCode', 
        'LongComment',
        'FipePercent',
        'GoodDeal',
        'HotDeal',
        'Specification.Title',
        'Specification.Make.id',
        'Specification.Make.Value',
        'Specification.Model.id',
        'Specification.Model.Value',
        'Specification.Version.id',
        'Specification.Version.Value',
        'Specification.YearFabrication',
        'Specification.YearModel',
        'Specification.Odometer',
        'Specification.Transmission',
        'Specification.NumberPorts',
        'Specification.BodyType',
        'Specification.VehicleAttributes',
        'Specification.Armored',
        'Specification.Color.IdPrimary',
        'Specification.Color.Primary',
        'Seller.SellerType',                                               
        'Seller.City',
        'Seller.State',
        'Prices.Price',
        'Prices.SearchPrice'                        
]

df = df[cols]

# rename of cols
df.columns = [string.replace('.', '_').replace('Specification_', '') for string in cols]

In [ ]:
df.head(3)

In [ ]:
df.dtypes

In [ ]:
## NA Values
df.isna().sum()[df.isna().sum()>0]

In [ ]:
df = df.fillna({'Version_Value' : '0.0'})

In [ ]:
df.Version_Value

In [ ]:
## Feature Engineering

# Motor" 1.0, 1.6, 2.0 etc. 
p = re.compile('[0-9]\.[0-9]')
motor_cil = df.Version_Value.apply(lambda x: p.search(x).group(0) if p.search(x) else 0)
df['motor'] = motor_cil


# Combustível; 
p = re.compile('flex|diesel|gasolina|alcool|álcool')
df.Version_Value



<h3> Case Studies: cars statics under xx.xxx price </h3>

In [ ]:
df_100k = df[df['Prices_Price'] <= 85000]

df_100k.describe().applymap(lambda x: round(x, 2))

In [ ]:
df_100k.head(3)

#### Quais fabricantes possuem, em média, carros mais novos, até a faixa dos 100k? 


In [ ]:

df_100k.groupby(['Make_Value'])[['Model_Value', 'YearModel', 'Odometer', 'Prices_Price']] \
    .agg(
        {'Model_Value': 'count',
        'YearModel': ['mean', 'min', 'max'],
        'Odometer': ['mean', 'min', 'max'],
        'Prices_Price': ['mean', 'min', 'max']
        }
        ).sort_values([('YearModel', 'mean'), ('Odometer', 'mean')], ascending=[False, False])

#### Lista dos modelos mais encontrados, por fabricante

In [ ]:
df_100k.groupby(['Make_Value', 'Model_Value'])[['Model_Value', 'YearModel', 'Odometer', 'Prices_Price']] \
    .agg(
        {'Model_Value': 'count',
        'YearModel': ['mean', 'min', 'max'],
        'Odometer': ['mean', 'min', 'max'],
        'Prices_Price': ['mean', 'min', 'max']
        }
        ).sort_values(['Make_Value', ('Model_Value', 'count')], ascending=[True, False])

In [ ]:
df_100k.groupby(['Make_Value', 'Model_Value'])[['Model_Value', 'YearModel', 'Odometer', 'Prices_Price']] \
    .agg({
        'Model_Value': [('model_count', 'count')],
        'YearModel': ['mean', 'min', 'max'],
        'Odometer': ['mean', 'min', 'max'],
        'Prices_Price': ['mean', 'min', 'max']}).sort_values(['Make_Value', ('Model_Value', 'model_count')], ascending=[True, False]).applymap(lambda x: round(x, 2) if isinstance(x, float)  else x)

In [ ]:
df.Seller_State[0].values

### My Search 

In [ ]:
#### carros até 80k e no estado de SP
df_70k = df[(df.Prices_Price <= 80000)
            & (df.YearModel >= 2018)
            & (df.Seller_State == 'São Paulo (SP)')
            & (df.Odometer <=70000)
            ]



df_70k.groupby(['Make_Value', 'Model_Value'])[['Model_Value', 'YearModel', 'Odometer', 'Prices_Price']] \
    .agg(
        {'Model_Value': 'count',
        'YearModel': ['mean', 'max', 'min'],
        'Odometer': ['mean', 'min', 'max'],
        'Prices_Price': ['mean', 'min', 'max']
        }
        ).sort_values(['Make_Value', ('YearModel', 'mean'), ('Prices_Price', 'mean')], ascending=[True, False, False])

In [ ]:
df.head(3)

In [ ]:
import seaborn as sns
from matplotlib import pyplot as plt

df_70k_model_count = df_70k[['Model_Value', 'YearModel']].groupby('Model_Value').agg( count = ('YearModel', 'count')).sort_values('count')


plt.figure(figsize=(12,10))
sns.barplot(df_70k_model_count, x = 'count', y = df_70k_model_count.index, width = 0.7)

plt.xticks(rotation=0)
plt.title("Carros até R$ 80k <70.000 km & >=2018")
plt.ylabel('Car Model')
plt.xlabel('Units Listed')

#plt.subplots_adjust(bottom=0.2) 
plt.show()

In [ ]:
df_70k